# ENV

pip install torch==1.13.1+cu116 torchvision==0.14.1+cu116 torchaudio==0.13.1 --extra-index-url https://download.pytorch.org/whl/cu116

pip install pyg_lib torch_sparse torch_scatter torch_cluster torch_spline_conv -f https://data.pyg.org/whl/torch-1.13.0+cu116.html

pip install 'numpy<2'



In [1]:
%load_ext autoreload
%autoreload 2
%reload_ext autoreload

import os
os.chdir("/home/dalai/GNN_E")

from scripts.models import *
import pandas as pd
from scripts.utils import *
from math import ceil
import gc


import torch
import torch.optim as optim

print(torch.cuda.is_available())
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)
print(torch.__version__)

/home/dalai/.conda/envs/gat_gpu/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


True
cuda
1.13.1+cu116


In [ ]:
# Load all movies with labels csv
df_all_movies = pd.read_csv("data/processed/all_movies_labelled_13_single.csv")
num_classes = 13 # based on df_movie choosen
batch_size = 16
half_wind_size = 4

In [ ]:
#df_train, df_test = split_train_test_vertically(df_all_movies, test_movies_dict = {"Sintel": 7, "TearsOfSteel": 10, "Superhero": 9})

df_train, df_test = split_train_test_horizontally(
    df_all_movies, 
    percentage_train = 0.8, 
    path_pickle_delay = "data/raw/labels/run_onsets.pkl", 
    path_movie_title_mapping = "data/raw/labels/category_mapping_movies.csv", 
    tr_len = 1.3
)

# Create a dataset
dataset_train = DatasetEmo(df=df_train, node_feat="symmetricwindow", sizewind=half_wind_size)
dataset_test = DatasetEmo(df=df_test, node_feat="symmetricwindow", sizewind=half_wind_size)

# Extarct the list of graphs of each dataset
graphs_list_train = dataset_train.get_graphs_list()
graphs_list_test = dataset_test.get_graphs_list()

# Create a dataloader
loader_train = pyg.loader.DataLoader(graphs_list_train, batch_size=batch_size, num_workers=4, persistent_workers=True)
loader_test = pyg.loader.DataLoader(graphs_list_test, batch_size=batch_size, num_workers=4, persistent_workers=True)

#Claulte number of batches
num_batches_train = ceil(len(graphs_list_train) / batch_size)
num_batches_test = ceil(len(graphs_list_test) / batch_size)

print(f"There are {len(graphs_list_train)} graphs in the train set.")
print(f"There are {len(graphs_list_test)} graphs in the test set.")
print(f"N batches in train: {num_batches_train}")
print(f"N batches in test: {num_batches_test}")



Movies in this df: [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13]
Creating the graph 0 1 0/232
Creating the graph 0 1 1/232
Creating the graph 0 1 2/232
Creating the graph 0 1 3/232
Creating the graph 0 1 4/232
Creating the graph 0 1 5/232
Creating the graph 0 1 6/232
Creating the graph 0 1 7/232
Creating the graph 0 1 8/232
Creating the graph 0 1 9/232
Creating the graph 0 1 10/232
Creating the graph 0 1 11/232
Creating the graph 0 1 12/232
Creating the graph 0 1 13/232
Creating the graph 0 1 14/232
Creating the graph 0 1 15/232
Creating the graph 0 1 16/232
Creating the graph 0 1 17/232
Creating the graph 0 1 18/232
Creating the graph 0 1 19/232
Creating the graph 0 1 20/232
Creating the graph 0 1 21/232
Creating the graph 0 1 22/232
Creating the graph 0 1 23/232
Creating the graph 0 1 24/232
Creating the graph 0 1 25/232
Creating the graph 0 1 26/232
Creating the graph 0 1 27/232
Creating the graph 0 1 28/232
Creating the graph 0 1 29/232
Creating the graph 0 1 30/232
Creating the grap

In [ ]:
def train(model, train_loader, num_epochs=10, learning_rate=0.001):

    losses = []

    # Set the model to training mode
    model.train()
    
    # Define the loss function (CrossEntropyLoss for multi-class classification)
    criterion = torch.nn.CrossEntropyLoss()
    
    # Define the optimizer (Adam)
    optimizer = optim.Adam(model.parameters(), lr=learning_rate)
    
    # Iterate through the number of epochs
    for epoch in range(num_epochs):
        total_loss = 0
        
        # Loop over the training data (train_loader is a PyTorch Geometric DataLoader)
        for i, batch in enumerate(train_loader):

            batch = batch.to(device)

            if (i+1)%100 == 0:
                print(f"Epoch {epoch+1}/{num_epochs}, Batch {i+1}")

            optimizer.zero_grad()  # Zero the gradients
            
            # Forward pass: Get predictions and attention weights
            out = model(batch)  # The model outputs the log-softmax scores
            
            # Compute the loss (CrossEntropyLoss automatically applies softmax internally)
            loss = criterion(out, batch.y)  # batch.y are the labels for the graph
            
            # Backward pass: Compute gradients
            loss.backward()
            
            # Update model parameters
            optimizer.step()
            
            # Accumulate loss for logging
            total_loss += loss.item()

            #print(torch.cuda.memory_summary(device=None, abbreviated=False))
            del batch  # Remove the batch object
            torch.cuda.empty_cache()  # Optionally, free unused memory
            #print(torch.cuda.memory_summary(device=None, abbreviated=False))


        # Print the loss after each epoch
        print(f"\tEpoch {epoch+1}/{num_epochs}, Loss: {total_loss / len(train_loader)}\n")
        losses.append(total_loss)

    return losses
        

In [ ]:
n_feat_per_node = graphs_list_train[0].x.shape[1]
MyGat = GATModel(input_dim = n_feat_per_node, 
                hidden_dim = num_classes, 
                output_dim = num_classes, 
                num_heads=num_classes)
MyGat = MyGat.to(device)

print(next(MyGat.parameters()).device)
gc.collect()
torch.cuda.empty_cache()
print(torch.cuda.memory_summary(device=None, abbreviated=False))


cuda:0
|===========================================================================|
|                  PyTorch CUDA memory summary, device ID 0                 |
|---------------------------------------------------------------------------|
|            CUDA OOMs: 2            |        cudaMalloc retries: 2         |
|===========================================================================|
|        Metric         | Cur Usage  | Peak Usage | Tot Alloc  | Tot Freed  |
|---------------------------------------------------------------------------|
| Allocated memory      |   26911 KB |    8563 MB |     870 GB |     870 GB |
|       from large pool |   26716 KB |    8562 MB |     870 GB |     870 GB |
|       from small pool |     194 KB |       3 MB |       0 GB |       0 GB |
|---------------------------------------------------------------------------|
| Active memory         |   26911 KB |    8563 MB |     870 GB |     870 GB |
|       from large pool |   26716 KB |    8562 MB |     8

In [ ]:
torch.cuda.empty_cache()
losses_train = train(model=MyGat, train_loader=loader_train)

Epoch 1/10, Batch 1
Epoch 1/10, Batch 2
Epoch 1/10, Batch 3
Epoch 1/10, Batch 4
Epoch 1/10, Batch 5
Epoch 1/10, Batch 6
Epoch 1/10, Batch 7
Epoch 1/10, Batch 8
Epoch 1/10, Batch 9
Epoch 1/10, Batch 10
Epoch 1/10, Batch 11
Epoch 1/10, Batch 12
Epoch 1/10, Batch 13
Epoch 1/10, Batch 14
Epoch 1/10, Batch 15
Epoch 1/10, Batch 16
Epoch 1/10, Batch 17
Epoch 1/10, Batch 18
Epoch 1/10, Batch 19
Epoch 1/10, Batch 20
Epoch 1/10, Batch 21
Epoch 1/10, Batch 22
Epoch 1/10, Batch 23
Epoch 1/10, Batch 24
Epoch 1/10, Batch 25
Epoch 1/10, Batch 26
Epoch 1/10, Batch 27
Epoch 1/10, Batch 28
Epoch 1/10, Batch 29
Epoch 1/10, Batch 30
Epoch 1/10, Batch 31
Epoch 1/10, Batch 32
Epoch 1/10, Batch 33
Epoch 1/10, Batch 34
Epoch 1/10, Batch 35
Epoch 1/10, Batch 36
Epoch 1/10, Batch 37
Epoch 1/10, Batch 38
Epoch 1/10, Batch 39
Epoch 1/10, Batch 40
Epoch 1/10, Batch 41
Epoch 1/10, Batch 42
Epoch 1/10, Batch 43
Epoch 1/10, Batch 44
Epoch 1/10, Batch 45
Epoch 1/10, Batch 46
Epoch 1/10, Batch 47
Epoch 1/10, Batch 48
E

# ***

In [16]:
del MyGat

In [17]:
batch_size = 16
loader_train = pyg.loader.DataLoader(graphs_list_train, batch_size=batch_size, num_workers=4, persistent_workers=True)
loader_test = pyg.loader.DataLoader(graphs_list_test, batch_size=batch_size, num_workers=4, persistent_workers=True)

#Claulte number of batches
num_batches_train = ceil(len(graphs_list_train) / batch_size)
num_batches_test = ceil(len(graphs_list_test) / batch_size)

print(f"There are {len(graphs_list_train)} graphs in the train set.")
print(f"There are {len(graphs_list_test)} graphs in the test set.")
print(f"N batches in train: {num_batches_train}")
print(f"N batches in test: {num_batches_test}")

There are 134765 graphs in the train set.
There are 87205 graphs in the test set.
N batches in train: 8423
N batches in test: 5451
